In [1]:
import collections
import datetime
import fluidsynth
import glob
import numpy as np
import pandas as pd
import seaborn as sns
import tensorflow as tf
import pretty_midi
import os
from IPython import display
from matplotlib import pyplot as plt
from typing import Dict, List, Optional, Sequence, Tuple

C:\Windows\system32\libfluidsynth.dll


In [2]:
import fluidsynth

In [3]:
seed=1234
tf.random.set_seed(seed)
np.random.seed(seed)

_SAMPLING_RATE=44100

In [4]:
sample_path=r"C:\Users\moonp\ASAC과정\MIDI_DATA\beatles_midi\beatles-believer.mid"
sample=pretty_midi.PrettyMIDI(sample_path)

In [5]:
def display_audio(pm: pretty_midi.PrettyMIDI, seconds=30):
  waveform = pm.fluidsynth(fs=_SAMPLING_RATE)
  # Take a sample of the generated waveform to mitigate kernel resets
  waveform_short = waveform[:seconds*_SAMPLING_RATE]
  return display.Audio(waveform_short, rate=_SAMPLING_RATE)

In [6]:
display_audio(sample)

In [7]:
print('Number of instruments:', len(sample.instruments))
tmp_inst=[]
for i in range(len(sample.instruments)):
    instrument = sample.instruments[i]
    instrument_name = pretty_midi.program_to_instrument_name(instrument.program)
    print('Instrument name:', instrument_name)
    tmp_inst.append(sample.instruments[i].program)

Number of instruments: 6
Instrument name: Acoustic Grand Piano
Instrument name: Acoustic Grand Piano
Instrument name: Acoustic Grand Piano
Instrument name: Acoustic Grand Piano
Instrument name: Acoustic Grand Piano
Instrument name: Acoustic Grand Piano


In [8]:
def midi_to_notes(midi_file: str) -> pd.DataFrame:
  pm = pretty_midi.PrettyMIDI(midi_file)
  instrument = pm.instruments[0]
  notes = collections.defaultdict(list)

  # Sort the notes by start time
  sorted_notes = sorted(instrument.notes, key=lambda note: note.start)
  prev_start = sorted_notes[0].start

  for note in sorted_notes:
    start = note.start
    end = note.end
    notes['pitch'].append(note.pitch)
    notes['start'].append(start)
    notes['end'].append(end)
    notes['step'].append(start - prev_start)
    notes['duration'].append(end - start)
    prev_start = start

  return pd.DataFrame({name: np.array(value) for name, value in notes.items()})

In [10]:
raw_notes = midi_to_notes(sample_path)
raw_notes.head()

pitch     start       end      step  duration
0     67  1.272726  2.905300  0.000000  1.632574
1     67  5.818176  6.178024  4.545450  0.359848
2     67  6.181812  6.541660  0.363636  0.359848
3     67  6.545448  6.905296  0.363636  0.359848
4     67  6.909084  7.268932  0.363636  0.359848

In [11]:
get_note_names = np.vectorize(pretty_midi.note_number_to_name)
sample_note_names = get_note_names(raw_notes['pitch'])
sample_note_names[:10]

array(['G4', 'G4', 'G4', 'G4', 'G4', 'A4', 'A4', 'C5', 'C5', 'B4'],
      dtype='<U3')

In [12]:
def notes_to_midi(
  notes: pd.DataFrame,
  out_file: str, 
  instrument_name: str,
  velocity: int = 100,  # note loudness
) -> pretty_midi.PrettyMIDI:

  pm = pretty_midi.PrettyMIDI()
  instrument = pretty_midi.Instrument(
      program=pretty_midi.instrument_name_to_program(
          instrument_name))

  prev_start = 0
  for i, note in notes.iterrows():
    start = float(prev_start + note['step'])
    end = float(start + note['duration'])
    note = pretty_midi.Note(
        velocity=velocity,
        pitch=int(note['pitch']),
        start=start,
        end=end,
    )
    instrument.notes.append(note)
    prev_start = start

  pm.instruments.append(instrument)
  pm.write(out_file)
  return pm

In [13]:
example_file = 'example.midi'
example_pm = notes_to_midi(
    raw_notes, out_file=example_file, instrument_name=instrument_name)

In [14]:
display_audio(example_pm)